# Проверка работоспособности ссылок

Этот скрипт облегчит Вам работу при проверки работоспособности внешних ссылок. Теперь Вам не нужно долго и упорно искать их в блокноте, отсеивать ссылки на сетевой и переходить по ним через колабовское окно с предупреждением о переходе. Скрипт пройдется за Вас по блокноту, соберет все ссылки, уберет повторы и ссылки на наш сетевой диск, а оставшиеся ссылки выведет списком, и их можно будет удобно и быстро прокликать.

Импортируем все необходимые библиотеки:

In [ ]:
import requests
import base64
import json

Для начала работы введите номер проверяемой ветви и свой GitHub Access Token в ячейку ниже и выполните её:

In [ ]:
github_token = "Input Your GitHub Access Token Here"
dev_branch = "dev-2.0"

Для dev-2.0 и далее список лекций задаем вручную:

In [ ]:
lectures = ['L01_Intro.ipynb', 'L02_Linear_models.ipynb', 'L03_Classic_ML.ipynb', 'L04_Feature_Engineering.ipynb', 'L05_Neural_networks.ipynb', 'L06_CNN.ipynb', 'L07_Learning_techniques.ipynb', 'L08_NN_architectures.ipynb', 'L09_RNN.ipynb', 'L10_Transformers.ipynb', 'L11_Segmentation_Detection.ipynb', 'L12_Representation_learning.ipynb', 'L13_Generative_models.ipynb', 'L14_Explainability.ipynb', 'L15_RL.ipynb']

Если Вам нужна более старая ветка, расскомментируйте и выполните код:

In [ ]:
# headers = {}
# if github_token:
#     headers['Authorization'] = f"token {github_token}"

# url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/?ref={dev_brunch}'
# r = requests.get(url, headers=headers)
# r.raise_for_status()
# data = r.json()
# lectures = [x['name'] for x in data[2:17]]

# print('Get lectures links')

In [ ]:
def get_links_from_lecture(lecture):

    print(lecture)

    headers = {}
    if github_token:
        headers['Authorization'] = f"token {github_token}"

    url = f'https://api.github.com/repos/EPC-MSU/EduNet-lectures/contents/out/{lecture}?ref={dev_branch}'
    r = requests.get(url, headers=headers)
    r.raise_for_status()
    data = r.json()
    file_content = data['content']
    file_content_encoding = data.get('encoding')
    if file_content_encoding == 'base64':
        file_content = base64.b64decode(file_content).decode()
    file_content = json.loads(file_content)

    clear_links = []
    temp_links = []
    for k in range(len(file_content["cells"])):
        cell_text = ','.join(file_content["cells"][k]['source'])
        one_cell = cell_text.split(" ")    # Делим нашу целую ячейку на какие-то части по пробелам, назовем их условно строками
        for i in range(0, len(one_cell)):  # И проверяем каждую такую строку
            if("http" in one_cell[i] and "edunet.kea.su" not in one_cell[i]):  # Если в строке есть ссылки
                n = one_cell[i].count("http")    # Сначала посчитаем количество ссылок в строке

                # Если в этой строке больше одной ссылки, то надо разделить
                # В этой части получим строку или список строк, начинающихся на "http"
                if(n>1):
                    s = one_cell[i].replace("http", " http")  # Добавим искусственно пробелы, чтобы по ним разделить, потому что вариант получше я пока не нашла
                    links_many = s.split(" ")
                    if ("http" not in  links_many[0]):
                        links_many.pop(0)
                    for i in range(0, len(links_many)):
                        temp_links.append(links_many[i])
                else:
                    links_one = one_cell[i][one_cell[i].find("http") :]
                    temp_links.append(links_one)

                # # А теперь попробуем убрать немного лишнего справа и свести в общий список по всем ячейкам
                for i in range(0, len(temp_links)):
                    if("\n" in temp_links[i]):
                        temp_links[i] = temp_links[i][ : temp_links[i].find("\n")]
                    if(")" in temp_links[i]):
                        temp_links[i] = temp_links[i][ : temp_links[i].find(")")]
                    if('"' in temp_links[i]):
                        temp_links[i] = temp_links[i][ : temp_links[i].find('"')]
                    # links_st2 = links_st1[ : links_st1.find(")<")]
                    # links_st3 = links_st2[ : links_st2.find('">')]
                    #clear_links.append(s_v1)
    print(len(temp_links), "links")
    set_links = set(temp_links)
    links=list(set_links)
    print(len(links), "unique links")
    for i in range(0, len(links)):
        print(i+1, ": ", links[i])

Присвойте переменной `lecture_num` номер проверяемой лекции от $1$ до $15$, в результате получите список всех внешних ссылок в лекции, не ведущих на наш сетевой диск

In [ ]:
lecture_num = 11
get_links_from_lecture(lectures[lecture_num-1])